In [4]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.ticker import FuncFormatter
import json # Added for reading ticker lists

from pathlib import Path
from datetime import datetime, timedelta

# ============================================
# CONFIGURATION
# ============================================
DATA_DIR = Path("data/5min_all")  # MODIFIED: directory containing {TICKER}.csv files (now 5min)
ACTIVE_TICKERS_FILE = Path("data/active_tickers.json") # ADDED
DELISTED_TICKERS_FILE = Path("data/delisted_tickers.json") # ADDED

START_DATE = "2023-01-01"       # YYYY-MM-DD
END_DATE = "2025-12-31"         # YYYY-MM-DD

TIMEZONE = 'America/Los_Angeles' # ADDED: Primary timezone for analysis
ORIGINAL_TIMESTAMP_TZ = 'UTC'    # ADDED: Assumed timezone of naive timestamps in CSVs, None if already tz-aware and correct

RTH_START_TIME = "06:30:00"     # ADDED: PST/PDT
RTH_END_TIME = "13:00:00"       # ADDED: PST/PDT (trades will exit at/after this time using last available RTH bar)

MIN_ENTRY_PRICE = 1.0           # Minimum stock price to consider for entry
PREV_CLOSE_MIN = 0.75           # ADDED: Minimum previous RTH close
AVG_DAILY_VOL_MAX = 15_000_000  # ADDED: Max 1-year average daily RTH volume
AVG_DAILY_VOL_WINDOW_DAYS = 252 # ADDED: Window for avg daily volume calculation
MIN_PERIODS_VOL_AVG = int(AVG_DAILY_VOL_WINDOW_DAYS * 0.8) # ADDED: Min periods for rolling vol avg

REINVEST_GAINS = False          # True to reinvest gains (compounding), False for fixed capital
PLOT_TRADE_DAYS_DEBUG = True    # True to plot individual trade days for debugging

INITIAL_CAPITAL = 1_000_000
POSITION_SIZE_PCT = 0.02        # 2% of account per position
STOP_LOSS_PCT = 0.05            # 5% stop-loss (for short: price moves up by 5%)
GAP_THRESHOLD = 0.30            # 30% gap-up
# EXIT_TIME = "15:30:00"        # REPLACED by RTH_END_TIME logic
MAX_TICKERS = 1                 # first N tickers with trades (for faster debugging)

# ============================================
# UTILITY: list all ticker CSV paths
# ============================================
def all_ticker_paths(data_dir: Path, active_f_path: Path, delisted_f_path: Path) -> list[Path]:
    """
    Returns a sorted list of CSV file paths for tickers found in active and delisted JSON files.
    Assumes JSON files are in the project root or path is absolute.
    """
    active_tickers = []
    delisted_tickers = []
    
    # Try to load active tickers
    try:
        if active_f_path.exists():
            with open(active_f_path, 'r') as f:
                active_tickers = json.load(f)
        else:
            print(f"Warning: Active tickers file not found at {active_f_path}")
    except Exception as e:
        print(f"Error loading active tickers from {active_f_path}: {e}")

    # Try to load delisted tickers
    try:
        if delisted_f_path.exists():
            with open(delisted_f_path, 'r') as f:
                delisted_tickers = json.load(f)
        else:
            print(f"Warning: Delisted tickers file not found at {delisted_f_path}")
    except Exception as e:
        print(f"Error loading delisted tickers from {delisted_f_path}: {e}")

    # all_tickers_set = set(str(t).upper() for t in active_tickers) | set(str(t).upper() for t in delisted_tickers)
    all_tickers_set = set(str(t).upper() for t in active_tickers)

    if not all_tickers_set:
        print("No tickers found in JSON files.")
        return []

    paths = []
    for ticker_symbol in sorted(list(all_tickers_set)):
        # Assuming CSV files are named {TICKER}.csv directly in data_dir
        p = data_dir / f"{ticker_symbol}.csv"
        if p.exists():
            paths.append(p)
        # else:
        #     print(f"Debug: CSV for ticker {ticker_symbol} not found at {p}") # Optional: for verbose missing file logs
    
    print(f"Found {len(paths)} existing CSV files for {len(all_tickers_set)} unique tickers from JSON lists.")
    return paths

# ============================================
# CORE: backtest logic for one ticker
# ============================================
def get_backtest_results_for_ticker(ticker: str, filepath: Path, start_date_str: str, end_date_str: str) -> tuple[
    pd.Series, dict, pd.Series, pd.Series
]:
    """
    Runs the backtest strategy for a single ticker.
    Args:
        ticker: The ticker symbol.
        filepath: Path to the ticker's CSV data file.
        start_date_str: Start date for backtesting (YYYY-MM-DD).
        end_date_str: End date for backtesting (YYYY-MM-DD).
    Returns:
        A tuple containing:
        - pnl_series: Series of realized PnL at exit times (index is PST).
        - trade_stats: Dictionary with trade statistics.
        - active_exposure_series: Series of allocated capital (index is PST).
        - active_count_series: Series indicating active positions (index is PST).
    """
    try:
        df_full_history = pd.read_csv(filepath, usecols=['timestamp', 'open', 'high', 'low', 'close', 'volume'])
    except FileNotFoundError:
        print(f"ERROR: File not found for {ticker} at {filepath}")
        # Create an empty index based on expected date range to avoid downstream errors if needed
        # For now, just return empty results.
        temp_idx = pd.date_range(start_date_str, end_date_str, freq='B', tz=TIMEZONE) # Dummy index
        return pd.Series(dtype=float, index=temp_idx).fillna(0.0), \
               {'num_trades': 0, 'num_stops': 0, 'num_wins': 0}, \
               pd.Series(dtype=float, index=temp_idx).fillna(0.0), \
               pd.Series(dtype=int, index=temp_idx).fillna(0)

    df_full_history.sort_values("timestamp", inplace=True)
    df_full_history.reset_index(drop=True, inplace=True)

    # --- Timestamp Conversion to Primary Timezone (PST/PDT) ---
    df_full_history["timestamp"] = pd.to_datetime(df_full_history["timestamp"])
    if df_full_history["timestamp"].dt.tz is None:
        if ORIGINAL_TIMESTAMP_TZ:
            df_full_history["timestamp"] = df_full_history["timestamp"].dt.tz_localize(ORIGINAL_TIMESTAMP_TZ)
        else: # Default to UTC if no original TZ is specified for naive timestamps
            print(f"Warning: Timestamps for {ticker} are naive. Assuming UTC based on ORIGINAL_TIMESTAMP_TZ=None or 'UTC'.")
            df_full_history["timestamp"] = df_full_history["timestamp"].dt.tz_localize('UTC')
    
    df_full_history["timestamp"] = df_full_history["timestamp"].dt.tz_convert(TIMEZONE)
    df_full_history.dropna(subset=['timestamp', 'open', 'high', 'low', 'close', 'volume'], inplace=True) # Drop rows with NaNs in critical columns
    if df_full_history.empty:
        print(f"No valid data for {ticker} after initial load and cleaning.")
        temp_idx = pd.date_range(start_date_str, end_date_str, freq='B', tz=TIMEZONE)
        return pd.Series(dtype=float, index=temp_idx).fillna(0.0), \
               {'num_trades': 0, 'num_stops': 0, 'num_wins': 0}, \
               pd.Series(dtype=float, index=temp_idx).fillna(0.0), \
               pd.Series(dtype=int, index=temp_idx).fillna(0)


    start_dt_obj = pd.to_datetime(start_date_str).date()
    end_dt_obj = pd.to_datetime(end_date_str).date()

    # Filter df for the backtest period based on PST dates
    df = df_full_history[
        (df_full_history["timestamp"].dt.date >= start_dt_obj) &
        (df_full_history["timestamp"].dt.date <= end_dt_obj)
    ].copy()

    # --- Create full_index based on PST timestamps within the filtered date range ---
    full_index = pd.DatetimeIndex([])
    if not df.empty:
        # Ensure full_index covers all unique timestamps within the start/end date RTH, even if no trades occur
        # This needs to span all potential timestamps where PnL could be recorded or exposure measured.
        # Create a full index of all timestamps within the date range of df
        all_valid_timestamps_in_range = df["timestamp"].drop_duplicates().sort_values()
        if not all_valid_timestamps_in_range.empty:
             full_index = pd.DatetimeIndex(all_valid_timestamps_in_range)

    empty_pnl = pd.Series(dtype=float, index=full_index).fillna(0.0)
    empty_exposure = pd.Series(dtype=float, index=full_index).fillna(0.0)
    empty_count = pd.Series(dtype=int, index=full_index).fillna(0)
    empty_stats = {'num_trades': 0, 'num_stops': 0, 'num_wins': 0}

    if df.empty:
        print(f"No data for {ticker} within specified date range {start_date_str} - {end_date_str}.")
        return empty_pnl, empty_stats, empty_exposure, empty_count
    
    df.loc[:, "date"] = df["timestamp"].dt.date # PST date
    df.reset_index(drop=True, inplace=True)

    # --- RTH Filtering and Pre-calculations ---
    rth_start_obj = datetime.strptime(RTH_START_TIME, "%H:%M:%S").time()
    rth_end_obj = datetime.strptime(RTH_END_TIME, "%H:%M:%S").time() # Exit target time

    # Filter df_full_history for RTH to calculate historical RTH stats
    df_full_rth = df_full_history[
        (df_full_history['timestamp'].dt.time >= rth_start_obj) &
        (df_full_history['timestamp'].dt.time < rth_end_obj) # Bars *starting* before RTH_END_TIME
    ].copy()

    if df_full_rth.empty:
        print(f"No RTH data available for {ticker} in its full history.")
        return empty_pnl, empty_stats, empty_exposure, empty_count
    
    df_full_rth.loc[:, 'date_col_rth'] = df_full_rth['timestamp'].dt.date

    # Previous RTH Close Lookup (based on last RTH bar of the day)
    prev_rth_closes_lookup = df_full_rth.groupby('date_col_rth').agg(
        prev_rth_close=("close", "last")
    ).reset_index()

    # Average Daily RTH Volume Lookup
    # Sum volume for each RTH day, then calculate rolling average
    daily_rth_volume = df_full_rth.groupby('date_col_rth')['volume'].sum()
    if daily_rth_volume.empty:
        print(f"No daily RTH volume data to process for {ticker}.")
        return empty_pnl, empty_stats, empty_exposure, empty_count

    # Shift(1) to ensure avg_vol is based on data up to T-1 for a trade on T
    avg_daily_rth_volume_lookup = daily_rth_volume.rolling(
                                window=AVG_DAILY_VOL_WINDOW_DAYS, 
                                min_periods=MIN_PERIODS_VOL_AVG
                                ).mean().shift(1) 


    # --- Prepare for Trading Loop ---
    # dates_to_process are PST dates from the 'df' which is already date-filtered
    dates_to_process = sorted(df["date"].unique()) 
    
    # all_historical_dates_pst for finding previous trading day robustly from full RTH history
    all_historical_dates_pst = sorted(df_full_rth["date_col_rth"].unique())


    realized_pnl_at_exit_dict = {}  
    active_exposure_dict = {}   
    active_count_dict = {}      
    
    num_total_trades = 0
    num_stop_loss_exits = 0
    num_winning_trades = 0

    parsed_rth_exit_target_time = rth_end_obj # Used to check if trade extends to EOD RTH

    for trade_date in dates_to_process: # trade_date is a datetime.date object (PST)
        actual_prev_trading_date_pst = None
        prev_rth_close_val = np.nan

        # Find the actual previous trading day that had RTH data
        try:
            current_trade_date_idx_in_hist_pst = all_historical_dates_pst.index(trade_date)
            if current_trade_date_idx_in_hist_pst > 0:
                actual_prev_trading_date_pst = all_historical_dates_pst[current_trade_date_idx_in_hist_pst - 1]
        except ValueError: # trade_date might not be in all_historical_dates_pst if it had no RTH data
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: not found in RTH historical dates (likely no RTH data on this day).")
            continue

        if actual_prev_trading_date_pst is None:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: no valid previous RTH trading day found.")
            continue
            
        # 1. Check Previous RTH Close Condition
        prev_close_series = prev_rth_closes_lookup[prev_rth_closes_lookup['date_col_rth'] == actual_prev_trading_date_pst]['prev_rth_close']
        if prev_close_series.empty or pd.isna(prev_close_series.iloc[0]) or prev_close_series.iloc[0] <= PREV_CLOSE_MIN:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: Prev RTH Close {prev_close_series.iloc[0] if not prev_close_series.empty else 'N/A'} <= {PREV_CLOSE_MIN} or not found.")
            continue
        prev_rth_close_val = prev_close_series.iloc[0]

        # 2. Check Average Daily RTH Volume Condition
        # avg_daily_rth_volume_lookup is indexed by date (PST)
        # We need volume average *before* trade_date, so lookup for trade_date (as shift(1) was used)
        current_avg_vol = avg_daily_rth_volume_lookup.get(trade_date) 
        if pd.isna(current_avg_vol) or current_avg_vol >= AVG_DAILY_VOL_MAX:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: Avg Daily RTH Vol {current_avg_vol:.0f} >= {AVG_DAILY_VOL_MAX} or not available.")
            continue

        # Get RTH data for the current trade_date
        df_day_rth = df_full_rth[df_full_rth['date_col_rth'] == trade_date].copy()
        df_day_rth.sort_values("timestamp", inplace=True) # timestamp is already PST
        
        if df_day_rth.empty:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: No RTH data for this day.")
            continue
        
        # Find RTH open bar
        entry_bar_candidates = df_day_rth[df_day_rth['timestamp'].dt.time == rth_start_obj]
        if entry_bar_candidates.empty:
            # Fallback: if no exact start time, take first bar on/after if desired, but for gaps usually precise start is needed
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: No RTH opening bar at {rth_start_obj}.")
            continue
        
        first_rth_bar = entry_bar_candidates.iloc[0]
        entry_ts = first_rth_bar["timestamp"] # PST timestamp
        entry_price = first_rth_bar["open"]
        
        if pd.isna(entry_price) or entry_price <= 0 or pd.isna(prev_rth_close_val) or prev_rth_close_val <= 0:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: Invalid entry price ({entry_price}) or prev_rth_close_val ({prev_rth_close_val}).")
            continue
        if entry_price < MIN_ENTRY_PRICE:
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: Entry price {entry_price} < {MIN_ENTRY_PRICE}.")
            continue
        
        # 3. Check Gap Condition
        gap_pct = (entry_price / prev_rth_close_val) - 1
        if gap_pct < GAP_THRESHOLD: # This is a short strategy on gap UP, so if it doesn't gap UP enough, skip.
            if PLOT_TRADE_DAYS_DEBUG: print(f"Skipping {trade_date} for {ticker}: Gap {gap_pct*100:.2f}% < {GAP_THRESHOLD*100:.2f}%. PrevClose: {prev_rth_close_val:.2f}, EntryOpen: {entry_price:.2f}")
            continue

        # --- Conditions met, prepare for trade ---
        num_total_trades += 1
        is_stop_exit_trade = False

        position_capital = INITIAL_CAPITAL * POSITION_SIZE_PCT
        shares = position_capital / entry_price
        stop_price = entry_price * (1 + STOP_LOSS_PCT) # Stop if price RISES (for short)

        exit_price_val = None   
        exit_ts_val = None      
        
        # Trade active bars are RTH bars from entry onwards for that day
        trade_active_bars_today = df_day_rth.loc[df_day_rth["timestamp"] >= entry_ts].copy()
        if trade_active_bars_today.empty: 
            if PLOT_TRADE_DAYS_DEBUG: print(f"Warning for {ticker} on {trade_date}: No trade active bars found after entry candidate. Undoing trade count.")
            num_total_trades -=1 
            continue

        for _, bar in trade_active_bars_today.iterrows():
            current_bar_ts = bar["timestamp"] # PST timestamp
            
            if pd.isna(bar["high"]) or pd.isna(bar["close"]): # Should not happen if df_full_history was cleaned
                continue  

            # Stop-loss check (price goes UP for short)
            if bar["high"] >= stop_price:
                exit_price_val = stop_price # Exit at stop price
                exit_ts_val = current_bar_ts
                is_stop_exit_trade = True
                break  
            
            # Time-based exit check (RTH End)
            # If current bar's start time is at or after RTH end target, exit with its close.
            # This means this bar is the last one to consider for timed exit.
            if current_bar_ts.time() >= parsed_rth_exit_target_time: 
                exit_price_val = bar["close"] 
                exit_ts_val = current_bar_ts
                break
        
        # If loop finished and no exit yet (e.g. parsed_rth_exit_target_time was not hit by any bar's start time)
        # this means the trade lasted till the very last RTH bar available for the day.
        if exit_price_val is None: 
            if not trade_active_bars_today.empty: 
                last_bar_for_trade = trade_active_bars_today.iloc[-1]
                if pd.notna(last_bar_for_trade["close"]) and pd.notna(last_bar_for_trade["timestamp"]):
                    exit_price_val = last_bar_for_trade["close"]
                    exit_ts_val = last_bar_for_trade["timestamp"]
                else: # Should not happen with clean data
                    if PLOT_TRADE_DAYS_DEBUG: print(f"Warning for {ticker} on {trade_date}: Last bar has NaN close/ts. Undoing trade count.")
                    num_total_trades -=1
                    continue
            else: # Should not happen if entry was made
                 if PLOT_TRADE_DAYS_DEBUG: print(f"Warning for {ticker} on {trade_date}: No bars for exit. Undoing trade count.")
                 num_total_trades -=1
                 continue

        if pd.isna(exit_price_val) or pd.isna(exit_ts_val) or exit_price_val <=0 :
            if PLOT_TRADE_DAYS_DEBUG: print(f"Warning for {ticker} on {trade_date}: Invalid exit price/ts. Undoing trade count. EP: {exit_price_val}, ETS: {exit_ts_val}")
            num_total_trades -=1 
            continue 

        if is_stop_exit_trade:
            num_stop_loss_exits += 1
        
        final_trade_pnl = (entry_price - exit_price_val) * shares # Short PnL
        if final_trade_pnl > 0: # Winning short trade
            num_winning_trades += 1
        
        # PnL is realized at exit_ts_val (which is PST)
        realized_pnl_at_exit_dict[exit_ts_val] = realized_pnl_at_exit_dict.get(exit_ts_val, 0) + final_trade_pnl

        # Mark exposure for bars where trade was active (all timestamps are PST)
        bars_trade_was_active = df_day_rth[
            (df_day_rth["timestamp"] >= entry_ts) & (df_day_rth["timestamp"] <= exit_ts_val)
        ]
        for active_bar_ts_loopvar in bars_trade_was_active["timestamp"]:
            active_exposure_dict[active_bar_ts_loopvar] = position_capital 
            active_count_dict[active_bar_ts_loopvar] = 1

        if PLOT_TRADE_DAYS_DEBUG:
            print(f"\n--- Debug Info for Trade on {ticker} {trade_date.strftime('%Y-%m-%d')} (PST) ---")
            print(f"Prev RTH Close ({actual_prev_trading_date_pst.strftime('%Y-%m-%d') if actual_prev_trading_date_pst else 'N/A'}): {prev_rth_close_val:.2f}")
            print(f"Avg Daily RTH Vol (1yr prior to {actual_prev_trading_date_pst.strftime('%Y-%m-%d')}): {current_avg_vol:,.0f}")
            print(f"Gap %: {gap_pct*100:.2f}%")
            print(f"Entry: {entry_price:.2f} at {entry_ts.strftime('%Y-%m-%d %H:%M:%S %Z')}")
            print(f"Exit:  {exit_price_val:.2f} at {exit_ts_val.strftime('%Y-%m-%d %H:%M:%S %Z')} {'(Stop Loss)' if is_stop_exit_trade else '(Time/EOD RTH Exit)'}")
            print(f"Stop Price Level (Short): {stop_price:.2f}")
            print(f"PnL for this trade: ${final_trade_pnl:,.2f}")

            plt.figure(figsize=(15, 7))
            
            # Plotting data range: Use df_full_history (which has 'timestamp' as PST)
            # Find indices in df_full_history for slicing based on PST timestamps
            try:
                entry_idx_full = df_full_history[df_full_history['timestamp'] == entry_ts].index[0]
                exit_idx_full = df_full_history[df_full_history['timestamp'] == exit_ts_val].index[0]
            except IndexError:
                print(f"Warning: Could not find entry/exit timestamp in df_full_history for trade on {trade_date}. Skipping debug plot.")
                # This can happen if entry_ts or exit_ts_val somehow isn't in df_full_history's 'timestamp' column,
                # which would be odd if they came from it. Or if they are from a bar not in the original df_full_history (e.g. synthetic stop).
                # Stop price is a level, actual exit is bar's timestamp.
                # For this plot, better to use RTH data for the day.
                plot_data_day = df_day_rth.copy() # df_day_rth has PST timestamps
                if plot_data_day.empty:
                    print(f"Warning: No RTH data to plot for debug trade on {trade_date}. Skipping debug plot.")
                    plt.close() # Close the empty figure
                    continue
                
                plt.plot(plot_data_day["timestamp"], plot_data_day["close"], label="Market Close Price (RTH)", color='blue', marker='.', linestyle='-')
                min_ts_plot, max_ts_plot = plot_data_day["timestamp"].min(), plot_data_day["timestamp"].max()

            else: # If indices found, plot a bit more context from df_full_history
                plot_start_idx = max(0, entry_idx_full - 10) # Show a few bars before entry
                plot_end_idx = min(len(df_full_history) - 1, exit_idx_full + 10) # Show a few bars after exit
                
                df_plot_data = df_full_history.iloc[plot_start_idx : plot_end_idx + 1].copy()

                if df_plot_data.empty:
                    print(f"Warning: No data to plot for debug trade on {trade_date}. Skipping debug plot.")
                    plt.close()
                    continue
                
                plt.plot(df_plot_data["timestamp"], df_plot_data["close"], label="Market Close Price (Context)", color='blue', marker='.', linestyle='-')
                min_ts_plot, max_ts_plot = df_plot_data["timestamp"].min(), df_plot_data["timestamp"].max()

            if pd.notna(prev_rth_close_val):
                plt.hlines(prev_rth_close_val, xmin=min_ts_plot, xmax=max_ts_plot, color='orange', linestyle=':', linewidth=2, label=f'Prev RTH Close ({prev_rth_close_val:.2f})')

            plt.scatter(entry_ts, entry_price, color='red', s=150, marker='v', zorder=5, edgecolors='black', label=f'Short Entry ({entry_price:.2f})') # Red for short
            plt.scatter(exit_ts_val, exit_price_val, color='green' if final_trade_pnl > 0 else 'darkred', s=150, marker='^' if final_trade_pnl > 0 else 'x', zorder=5, linewidths=2, label=f'Cover ({exit_price_val:.2f})') # Green for profit
            
            stop_line_xmin = max(min_ts_plot, entry_ts)
            stop_line_xmax = min(max_ts_plot, exit_ts_val) 
            if stop_line_xmax >= stop_line_xmin : 
                plt.hlines(stop_price, xmin=stop_line_xmin, xmax=stop_line_xmax, color='magenta', linestyle='--', linewidth=2, label=f'Stop Loss ({stop_price:.2f})')

            plt.title(f"Trade Debug: {ticker} on {trade_date.strftime('%Y-%m-%d')} (PST) | PnL: ${final_trade_pnl:,.2f}")
            plt.xlabel(f"Timestamp ({TIMEZONE})")
            plt.ylabel("Price")
            plt.legend(loc='best')
            plt.grid(True, linestyle='--', alpha=0.7)
            plt.tight_layout()
            plt.show()

    trade_stats = {
        'num_trades': num_total_trades,
        'num_stops': num_stop_loss_exits,
        'num_wins': num_winning_trades
    }
    
    # Reindex results to the full_index (which is PST based)
    pnl_series = pd.Series(realized_pnl_at_exit_dict).sort_index().reindex(full_index, fill_value=0.0)
    active_exposure_series = pd.Series(active_exposure_dict).sort_index().reindex(full_index, fill_value=0.0)
    active_count_series = pd.Series(active_count_dict).sort_index().reindex(full_index, fill_value=0).astype(int)

    return pnl_series, trade_stats, active_exposure_series, active_count_series

def compute_metrics(pnl_series: pd.Series, initial_capital: float) -> dict:
    """
    Computes performance metrics from a PnL series.
    Args:
        pnl_series: Series of realized PnL at exit times (PST index).
        initial_capital: The starting capital for the backtest.
    Returns:
        A dictionary of performance metrics.
    """
    empty_metrics_dict = {
        "final_cum_pnl": 0.0, "total_pct_return": 0.0,
        "annual_return": 0.0, "annual_volatility": 0.0,
        "sharpe_ratio": np.nan,
        "daily_returns": pd.Series(dtype=float, index=pd.DatetimeIndex([], tz=TIMEZONE)), # Ensure tz-aware
    }
    if pnl_series.empty or pnl_series.abs().sum() == 0:    
        return empty_metrics_dict

    # Ensure index is DatetimeIndex and tz-aware (should be from get_backtest_results)
    if not isinstance(pnl_series.index, pd.DatetimeIndex):
        pnl_series.index = pd.to_datetime(pnl_series.index)
    if pnl_series.index.tz is None: # Should not happen if full_index was tz-aware
        pnl_series.index = pnl_series.index.tz_localize(TIMEZONE) # Or UTC if that was the standard
    elif pnl_series.index.tz.zone != TIMEZONE: # Convert if different timezone
        pnl_series.index = pnl_series.index.tz_convert(TIMEZONE)


    intraday_equity_curve = pnl_series.cumsum() 
    if intraday_equity_curve.empty:    
        return empty_metrics_dict

    final_cum_pnl = intraday_equity_curve.iloc[-1]
    total_pct_return = final_cum_pnl / initial_capital if initial_capital != 0 else 0.0
    
    # EOD equity based on PST dates
    eod_equity = intraday_equity_curve.groupby(intraday_equity_curve.index.date).last()
    eod_equity.index = pd.to_datetime(eod_equity.index).tz_localize(TIMEZONE) # Restore tz for index after groupby date

    daily_pnl_changes = pd.Series(dtype=float, index=pd.DatetimeIndex([], tz=TIMEZONE)) 
    if not eod_equity.empty:
        daily_pnl_changes_temp = eod_equity.diff() 
        if not daily_pnl_changes_temp.empty:  
            daily_pnl_changes_temp.iloc[0] = eod_equity.iloc[0] 
        else: # Only one day of EOD equity
            daily_pnl_changes_temp = pd.Series([eod_equity.iloc[0]], index=[eod_equity.index[0]])
        
        # Reindex to business days to correctly annualize (ensuring index is tz-aware)
        if not daily_pnl_changes_temp.empty:
            start_date_metric = daily_pnl_changes_temp.index.min()
            end_date_metric = daily_pnl_changes_temp.index.max()   
            if pd.NaT not in [start_date_metric, end_date_metric] and start_date_metric <= end_date_metric: 
                # bdate_range is tz-naive, so add tz back
                bdate_idx = pd.bdate_range(start=start_date_metric.normalize(), end=end_date_metric.normalize()).tz_localize(TIMEZONE)
                if not bdate_idx.empty:  
                    daily_pnl_changes = daily_pnl_changes_temp.reindex(bdate_idx, fill_value=0.0)
    
    daily_returns = pd.Series(dtype=float, index=pd.DatetimeIndex([], tz=TIMEZONE)) 
    if not daily_pnl_changes.empty: 
        daily_returns = daily_pnl_changes / initial_capital if initial_capital != 0 else daily_pnl_changes * 0

    annual_return_val, annual_volatility_val, sharpe_ratio_val = 0.0, 0.0, np.nan
    if not daily_returns.empty and daily_returns.abs().sum() != 0 :
        mean_daily = daily_returns.mean()
        std_daily = daily_returns.std(ddof=0) # Population standard deviation
            
        annual_return_val = mean_daily * 252
        if std_daily == 0:  
            annual_volatility_val = 0.0
            if mean_daily == 0 : sharpe_ratio_val = 0.0  
            else: sharpe_ratio_val = np.inf * np.sign(mean_daily) # Or undefined based on preference
        else:
            annual_volatility_val = std_daily * np.sqrt(252)
            sharpe_ratio_val = annual_return_val / annual_volatility_val
        
    return {
        "final_cum_pnl": final_cum_pnl, "total_pct_return": total_pct_return,
        "annual_return": annual_return_val, "annual_volatility": annual_volatility_val,
        "sharpe_ratio": sharpe_ratio_val,
        "daily_returns": daily_returns, # This is now tz-aware (PST)
    }

# ============================================
# MAIN: process tickers, aggregate results, and plot
# ============================================
def main():
    """Main function to run the backtest, aggregate results, and generate plots."""
    # Use new all_ticker_paths
    ticker_paths = all_ticker_paths(DATA_DIR, ACTIVE_TICKERS_FILE, DELISTED_TICKERS_FILE)
    if not ticker_paths:
        print(f"No CSV files found based on JSON lists in {DATA_DIR} and related JSON files. Please provide data and valid JSON lists.")
        return

    summaries = []              
    all_ticker_pnl_series = {}  # Store PnL series (PST indexed)
    all_ticker_exposure_series = [] 
    all_ticker_count_series = []    

    processed_tickers_count = 0

    for path in ticker_paths:
        if processed_tickers_count >= MAX_TICKERS and MAX_TICKERS > 0: # MAX_TICKERS=0 or negative means process all
            print(f"Reached MAX_TICKERS limit of {MAX_TICKERS}. Stopping further processing.")
            break

        ticker = path.stem # Assumes filename is TICKER.csv
        print(f"\nProcessing {ticker}...")
        pnl_series, trade_stats, active_exposure_s, active_count_s = get_backtest_results_for_ticker(
            ticker, path, START_DATE, END_DATE
        )
        
        if trade_stats['num_trades'] == 0 :  
            if not PLOT_TRADE_DAYS_DEBUG: # If debug is on, get_backtest might print reasons for no trades
                print(f"No trades for {ticker} (conditions or filters not met within date range {START_DATE} to {END_DATE}). Skipping.")
            # else it will print detailed skips if PLOT_TRADE_DAYS_DEBUG is true from within the function
            continue # Skip if no trades

        # Ensure all series have a tz-aware DatetimeIndex (should be PST from get_backtest_results)
        for s in [pnl_series, active_exposure_s, active_count_s]:
            if not isinstance(s.index, pd.DatetimeIndex): s.index = pd.to_datetime(s.index)
            if s.index.tz is None: s.index = s.index.tz_localize(TIMEZONE)
            elif s.index.tz.zone != TIMEZONE : s.index = s.index.tz_convert(TIMEZONE)

        all_ticker_pnl_series[ticker] = pnl_series 
        if not active_exposure_s.empty:
            all_ticker_exposure_series.append(active_exposure_s)
        if not active_count_s.empty:
            all_ticker_count_series.append(active_count_s)

        metrics = compute_metrics(pnl_series, INITIAL_CAPITAL) 
        metrics["ticker"] = ticker
        metrics["trade_stats"] = trade_stats 
        summaries.append(metrics)
        processed_tickers_count += 1
        print(f"Finished processing {ticker}. Trades: {trade_stats['num_trades']}. PnL: {metrics['final_cum_pnl']:.2f}")


    if not summaries:
        print(f"No tickers generated trades or valid PnL within date range {START_DATE} to {END_DATE} after processing all available files (or up to MAX_TICKERS).")
        return

    # --- Individual Ticker Statistics ---
    df_summary_list = []
    for s_item in summaries:
        ts = s_item["trade_stats"]
        num_trades = ts.get('num_trades',0)
        num_stops = ts.get('num_stops',0)
        num_wins = ts.get('num_wins',0)
        num_time_exits = num_trades - num_stops
        win_rate = (num_wins / num_trades) * 100 if num_trades > 0 else 0.0
        
        df_summary_list.append({
            "Ticker": s_item["ticker"], "Num Trades": num_trades, "Stops": num_stops,
            "Time Exits": num_time_exits, "Wins": num_wins, "Win Rate %": win_rate,
            "Final Cum PnL": s_item["final_cum_pnl"],
            "Total % Return": s_item["total_pct_return"] * 100,
            "Annual Return %": s_item["annual_return"] * 100,
            "Annual Volatility %": s_item["annual_volatility"] * 100,
            "Sharpe": s_item["sharpe_ratio"],
        })
    df_summary = pd.DataFrame(df_summary_list)
    if not df_summary.empty:
        df_summary = df_summary.set_index("Ticker")

    print(f"\nIndividual Ticker Statistics (Processed {len(summaries)} Tickers, Period: {START_DATE} to {END_DATE}):\n")
    if not df_summary.empty:
        print(df_summary.to_string(float_format="{:.2f}".format))
    else:
        print("No individual ticker data to display.")

    # --- Aggregate Portfolio Statistics ---
    # All series (PnL, daily returns) are PST indexed. Concat will align them.
    total_portfolio_trades = sum(s['trade_stats'].get('num_trades',0) for s in summaries)
    total_portfolio_stops = sum(s['trade_stats'].get('num_stops',0) for s in summaries)
    total_portfolio_wins = sum(s['trade_stats'].get('num_wins',0) for s in summaries)
    total_portfolio_time_exits = total_portfolio_trades - total_portfolio_stops
    aggregate_win_rate = (total_portfolio_wins / total_portfolio_trades) * 100 if total_portfolio_trades > 0 else 0.0
    
    sum_of_individual_final_pnl = sum(s['final_cum_pnl'] for s in summaries)

    annual_return_agg, annual_volatility_agg, sharpe_ratio_agg = 0.0, 0.0, np.nan
    total_pct_return_agg = sum_of_individual_final_pnl / INITIAL_CAPITAL if INITIAL_CAPITAL != 0 else 0.0 # Default for fixed capital

    # Portfolio PnL per bar (sum of PnL from all tickers for each bar)
    # Ensure all_ticker_pnl_series have common tz-aware index or can be aligned.
    # They should all be PST indexed from get_backtest_results_for_ticker.
    portfolio_realized_pnl_per_bar = pd.Series(dtype=float, index=pd.DatetimeIndex([], tz=TIMEZONE)) 
    if all_ticker_pnl_series:
        valid_pnl_series_list = [s for s in all_ticker_pnl_series.values() if not s.empty and s.abs().sum() > 0]
        if valid_pnl_series_list:
            # Concat aligns by index; ensure they are all compatible (PST datetime index)
            df_all_realized_pnl = pd.concat(valid_pnl_series_list, axis=1).fillna(0.0)
            portfolio_realized_pnl_per_bar = df_all_realized_pnl.sum(axis=1)

    # Ensure portfolio_realized_pnl_per_bar has a sorted tz-aware index
    if not portfolio_realized_pnl_per_bar.empty:
        portfolio_realized_pnl_per_bar = portfolio_realized_pnl_per_bar.sort_index()
        if not isinstance(portfolio_realized_pnl_per_bar.index, pd.DatetimeIndex):
             portfolio_realized_pnl_per_bar.index = pd.to_datetime(portfolio_realized_pnl_per_bar.index)
        if portfolio_realized_pnl_per_bar.index.tz is None:
            portfolio_realized_pnl_per_bar.index = portfolio_realized_pnl_per_bar.index.tz_localize(TIMEZONE)
        elif portfolio_realized_pnl_per_bar.index.tz.zone != TIMEZONE:
            portfolio_realized_pnl_per_bar.index = portfolio_realized_pnl_per_bar.index.tz_convert(TIMEZONE)


    if REINVEST_GAINS:
        if not portfolio_realized_pnl_per_bar.empty:
            portfolio_equity_curve_intraday = INITIAL_CAPITAL + portfolio_realized_pnl_per_bar.cumsum()
            # EOD equity based on PST dates
            eod_portfolio_equity = portfolio_equity_curve_intraday.groupby(portfolio_equity_curve_intraday.index.date).last()
            eod_portfolio_equity.index = pd.to_datetime(eod_portfolio_equity.index).tz_localize(TIMEZONE)
            
            if not eod_portfolio_equity.empty:
                min_date_equity = eod_portfolio_equity.index.min().normalize()
                max_date_equity = eod_portfolio_equity.index.max().normalize()
                if pd.NaT not in [min_date_equity, max_date_equity] and min_date_equity <= max_date_equity: 
                    all_trading_days_idx = pd.bdate_range(start=min_date_equity, end=max_date_equity).tz_localize(TIMEZONE)
                    if not all_trading_days_idx.empty:
                        eod_portfolio_equity_reindexed = eod_portfolio_equity.reindex(all_trading_days_idx).ffill().fillna(INITIAL_CAPITAL)
                        
                        daily_portfolio_pnl_dollar = eod_portfolio_equity_reindexed.diff()
                        if not daily_portfolio_pnl_dollar.empty: 
                            daily_portfolio_pnl_dollar.iloc[0] = eod_portfolio_equity_reindexed.iloc[0] - INITIAL_CAPITAL
                        
                        start_of_day_equity = eod_portfolio_equity_reindexed.shift(1).fillna(INITIAL_CAPITAL)
                        # Avoid division by zero or near-zero if equity flatlines at 0
                        valid_sod_equity = start_of_day_equity[start_of_day_equity.abs() > 1e-6] 
                        
                        if not daily_portfolio_pnl_dollar.empty and not valid_sod_equity.empty:
                            # Align indices before division
                            daily_pnl_aligned, sod_equity_aligned = daily_portfolio_pnl_dollar.align(valid_sod_equity, join='inner')
                            if not sod_equity_aligned.empty:
                                reinvested_daily_returns = (daily_pnl_aligned / sod_equity_aligned).replace([np.inf, -np.inf], np.nan).dropna()

                                if not reinvested_daily_returns.empty and reinvested_daily_returns.abs().sum() != 0:
                                    mean_daily_agg = reinvested_daily_returns.mean()
                                    std_daily_agg = reinvested_daily_returns.std(ddof=0)
                                    annual_return_agg = mean_daily_agg * 252
                                    if std_daily_agg == 0:
                                        annual_volatility_agg = 0.0
                                        sharpe_ratio_agg = np.inf * np.sign(mean_daily_agg) if mean_daily_agg != 0 else 0.0
                                    else:
                                        annual_volatility_agg = std_daily_agg * np.sqrt(252)
                                        sharpe_ratio_agg = annual_return_agg / annual_volatility_agg
            
            if not portfolio_equity_curve_intraday.empty:  
                total_pct_return_agg = (portfolio_equity_curve_intraday.iloc[-1] - INITIAL_CAPITAL) / INITIAL_CAPITAL if INITIAL_CAPITAL != 0 else 0.0
    else: # Fixed Capital
        # Sum of daily returns from individual tickers (they are % of initial capital)
        aggregate_daily_returns_list = [s["daily_returns"] for s in summaries if not s["daily_returns"].empty]
        if aggregate_daily_returns_list:
            # Ensure all daily_returns series are compatible (PST tz-aware index)
            aligned_returns = []
            for dr_series in aggregate_daily_returns_list:
                if not isinstance(dr_series.index, pd.DatetimeIndex): dr_series.index = pd.to_datetime(dr_series.index)
                if dr_series.index.tz is None: dr_series.index = dr_series.index.tz_localize(TIMEZONE)
                elif dr_series.index.tz.zone != TIMEZONE: dr_series.index = dr_series.index.tz_convert(TIMEZONE)
                aligned_returns.append(dr_series)

            if aligned_returns:
                df_daily_returns_agg = pd.concat(aligned_returns, axis=1).fillna(0.0)
                if not df_daily_returns_agg.empty:
                    # Ticker names for columns if needed for debugging, not essential for sum
                    # tickers_with_returns = [s["ticker"] for s in summaries if not s["daily_returns"].empty and s["ticker"] in all_ticker_pnl_series]
                    # if len(tickers_with_returns) == df_daily_returns_agg.shape[1]:
                    #     df_daily_returns_agg.columns = tickers_with_returns
                    
                    portfolio_daily_returns_fixed_cap = df_daily_returns_agg.sum(axis=1)

                    if not portfolio_daily_returns_fixed_cap.empty and portfolio_daily_returns_fixed_cap.abs().sum() !=0:
                        mean_daily_agg = portfolio_daily_returns_fixed_cap.mean()
                        std_daily_agg = portfolio_daily_returns_fixed_cap.std(ddof=0)
                        annual_return_agg = mean_daily_agg * 252
                        if std_daily_agg == 0:
                            annual_volatility_agg = 0.0
                            sharpe_ratio_agg = np.inf * np.sign(mean_daily_agg) if mean_daily_agg != 0 else 0.0
                        else:
                            annual_volatility_agg = std_daily_agg * np.sqrt(252)
                            sharpe_ratio_agg = annual_return_agg / annual_volatility_agg
    
    print(f"\nAggregate Portfolio Statistics (Processed {len(summaries)} Tickers, Period: {START_DATE} to {END_DATE}):\n")
    print(f"Capital Management: {'Reinvest Gains' if REINVEST_GAINS else 'Fixed Capital'}")
    print(f"Timezone for Analysis: {TIMEZONE}")
    print(f"RTH: {RTH_START_TIME} - {RTH_END_TIME}")
    print(f"Number of tickers included: {len(summaries)}")
    print(f"Total Trades:               {total_portfolio_trades}")
    print(f"Total Stops:                {total_portfolio_stops}")
    print(f"Total Time Exits (RTH EOD): {total_portfolio_time_exits}")
    print(f"Total Wins:                 {total_portfolio_wins}")
    print(f"Aggregate Win Rate %:       {aggregate_win_rate:.2f}%")
    print(f"Sum of Individual Final PnL:${sum_of_individual_final_pnl:,.2f}") # This is sum of non-compounded PnLs
    print(f"Portfolio Total % Return:   {total_pct_return_agg*100:.2f}%") # Based on fixed or reinvested capital
    print(f"Agg. Annual Return %:       {annual_return_agg*100:.2f}%")  
    print(f"Agg. Annual Volatility %:   {annual_volatility_agg*100:.2f}%")
    print(f"Agg. Sharpe Ratio:          {sharpe_ratio_agg:.2f}")

    # --- Plotting ---
    # Equity curve plot (based on portfolio_realized_pnl_per_bar, which is sum of individual PnLs, suitable for fixed capital view or basis for reinvested)
    if not portfolio_realized_pnl_per_bar.empty:
        equity_for_plot = INITIAL_CAPITAL + portfolio_realized_pnl_per_bar.cumsum()
        # If REINVEST_GAINS, portfolio_equity_curve_intraday would be the more accurate equity curve
        if REINVEST_GAINS and 'portfolio_equity_curve_intraday' in locals() and not portfolio_equity_curve_intraday.empty :
             equity_for_plot = portfolio_equity_curve_intraday

        cum_pct_for_plot = (equity_for_plot - INITIAL_CAPITAL) / INITIAL_CAPITAL if INITIAL_CAPITAL != 0 else pd.Series(0.0, index=equity_for_plot.index)

        plt.figure(figsize=(12, 7))
        plt.plot(cum_pct_for_plot.index, cum_pct_for_plot.values, label="Aggregate Portfolio %PnL")
        plt.axhline(0, color="gray", linewidth=0.8, linestyle="--")
        plot_title_suffix = f" (Period: {START_DATE} to {END_DATE}, {TIMEZONE})"
        plot_title_suffix += f" ({'Reinvested' if REINVEST_GAINS else 'Fixed'} Capital)"
        plt.title(f"Aggregate Cumulative %PnL{plot_title_suffix}")
        plt.xlabel(f"Timestamp ({TIMEZONE})")
        plt.ylabel("Cumulative PnL (%)")
        plt.gca().yaxis.set_major_formatter(FuncFormatter(lambda y, _: f"{y*100:.1f}%"))
        plt.legend()
        plt.grid(True, linewidth=0.5, linestyle="--", alpha=0.7)
        plt.tight_layout()
        plt.show()
    else:
        print("No aggregate PnL data available for plotting equity curve.")

    # Plotting active positions (all series should be PST indexed)
    if all_ticker_count_series:
        df_all_counts = pd.concat(all_ticker_count_series, axis=1).fillna(0).astype(int)
        if not df_all_counts.empty:
            portfolio_intraday_active_positions = df_all_counts.sum(axis=1).sort_index()
            if not portfolio_intraday_active_positions.empty:
                # Resample to daily max using PST dates
                portfolio_daily_max_positions = portfolio_intraday_active_positions.resample('D').max().fillna(0).astype(int)
                if not portfolio_daily_max_positions.empty and portfolio_daily_max_positions.sum() > 0 : 
                    plt.figure(figsize=(12, 7))
                    plt.plot(portfolio_daily_max_positions.index, portfolio_daily_max_positions.values, drawstyle='steps-post', label='Max Concurrent Open Positions')
                    plt.title(f'Daily Max Concurrent Open Positions (Period: {START_DATE} to {END_DATE}, {TIMEZONE})')
                    plt.xlabel(f'Date ({TIMEZONE})')
                    plt.ylabel('Number of Positions')
                    plt.legend()
                    plt.grid(True, linewidth=0.5, linestyle="--", alpha=0.7)
                    plt.tight_layout()
                    plt.show()
                else: print("No daily max position data to plot (all zeros or empty after resample).")
            else: print("No intraday active count data to resample for daily positions plot.")
        else: print("No combined active count data available.")
    else:
        print("No active count data from any ticker for plotting number of positions.")

    # Plotting allocated capital (all series should be PST indexed)
    if all_ticker_exposure_series:
        df_all_exposure = pd.concat(all_ticker_exposure_series, axis=1).fillna(0.0)
        if not df_all_exposure.empty:
            portfolio_intraday_total_allocated_capital = df_all_exposure.sum(axis=1).sort_index()
            if not portfolio_intraday_total_allocated_capital.empty:
                portfolio_daily_max_allocated_capital = portfolio_intraday_total_allocated_capital.resample('D').max().fillna(0.0)
                if not portfolio_daily_max_allocated_capital.empty and portfolio_daily_max_allocated_capital.abs().sum() > 0 : 
                    plt.figure(figsize=(12, 7))
                    plt.plot(portfolio_daily_max_allocated_capital.index, portfolio_daily_max_allocated_capital.values, drawstyle='steps-post', label='Daily Max Allocated Capital')
                    plt.title(f'Daily Maximum Allocated Capital (Period: {START_DATE} to {END_DATE}, {TIMEZONE})')
                    plt.xlabel(f'Date ({TIMEZONE})')
                    plt.ylabel('Total Allocated Capital ($)')
                    plt.gca().yaxis.set_major_formatter(FuncFormatter(lambda x, p: f'${x:,.0f}')) 
                    plt.legend()
                    plt.grid(True, linewidth=0.5, linestyle="--", alpha=0.7)
                    plt.tight_layout()
                    plt.show()
                else: print("No daily max allocated capital data to plot (all zeros or empty after resample).")
            else: print("No intraday exposure data to resample for daily exposure plot.")
        else: print("No combined exposure data available.")
    else:
        print("No exposure data from any ticker for plotting position value.")


if __name__ == "__main__":
    # Ensure DATA_DIR exists
    if not DATA_DIR.exists():
        print(f"Data directory '{DATA_DIR}' does not exist. Please create it.")
        # Attempt to create for convenience if it's a common case (e.g. first run)
        try:
            DATA_DIR.mkdir(parents=True, exist_ok=True)
            print(f"Created data directory: {DATA_DIR}")
        except Exception as e:
            print(f"Could not create data directory {DATA_DIR}: {e}")
            exit() # Exit if data dir cannot be accessed/created
            
    # Check for JSON files (assuming they are in the current working directory or root of project)
    # If these files are critical and not found, could add an exit() here.
    if not ACTIVE_TICKERS_FILE.exists():
        print(f"Warning: Active tickers file '{ACTIVE_TICKERS_FILE}' not found. Expecting it in script directory or as specified.")
    if not DELISTED_TICKERS_FILE.exists():
        print(f"Warning: Delisted tickers file '{DELISTED_TICKERS_FILE}' not found. Expecting it in script directory or as specified.")
        
    main()

Found 8276 existing CSV files for 11463 unique tickers from JSON lists.

Processing A...
No data for A within specified date range 2023-01-01 - 2025-12-31.

Processing AA...
No data for AA within specified date range 2023-01-01 - 2025-12-31.

Processing AAA...
Skipping 2023-01-09 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-10 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-11 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-12 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-16 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-18 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-19 for AAA: not found in RTH historical dates (likely no RTH data on this day).
Skipping 2023-01-25 for AAA: not found in RTH historical dat

KeyboardInterrupt: 